## This is the final Noteebok to be used for following :- 

- ### Word to HTML conversion and zip file creation for all types of documents.
- ### Final conversion/parsing of documents (zip files) for all types of documents.
<br>

## Steps for executing this notebook

1. Open terminal and change cwd to "conversion/code" directory.
2. Run command <i> jupyter notebook </i>
3. On the jupyter notebook, open the <i>dev notebook final v10.ipynb</i> notebook.
4. Execute first code cell #1  for importing the basis module and changing the dir to the correct path.<br><i> Please note, never run this cell multiple times in a kernel session <i>

### Word to HTML Conversion

- Run cell #2 , this will convert all the word files present at "conversion\data\ingest" to HTML and create a zip file for each document.

### Document Conversion 

- Run Cells #3, #4, #5 , These cell will create the required functions for the conversion process.

- Function RunAll (Dev) and RunAllTest (Test) are used for executing the conversion process in the respective environments.

- For example all the cell starting from cell #6 and beyond have examples on how to run these function.

- This function take a list of zip file names as input parameter.

In [1]:
import os
import zipfile
%load_ext autoreload

%autoreload 2
os.chdir(os.path.abspath(os.path.join('..')))

In [ ]:
# WORD to HTML Conversion 
###################################
##########  STEP 0  ###############

from wordToHtmlConvertor.wordToHtmlConvertor import WordToHtmlConvertor

wordToHtmlConvertorObj = WordToHtmlConvertor()
wordToHtmlConvertorObj.convertWordToHTML()

############# END #################

In [ ]:
import tracemalloc
import psutil
import pprint
import pandas as pd
import uuid
import json
import os
import glob
import re
import sys
from bs4 import NavigableString, BeautifulSoup
from collections import defaultdict
import random
import string
import time

from utils.config import config
from utils.logger.logger import loggerCreator

# ePI Modules
from parse.rulebook.rulebook import StyleRulesDictionary

from parse.extractor.parser import parserExtractor
from match.matchDocument.matchDocument import MatchDocument
from documentAnnotation.documentAnnotation import DocumentAnnotation
from htmlDocTypePartitioner.partition import DocTypePartitioner
from extractContentBetweenHeadings.dataBetweenHeadingsExtractor import DataBetweenHeadingsExtractor
from fhirXmlGenerator.fhirXmlGenerator import FhirXmlGenerator
from fhirService.fhirService import FhirService
from utils.logger.matchLogger import MatchLogger
from languageInfo.documentTypeNames.documentTypeNames import DocumentTypeNames
from listBundle.addAndUpdateListBundle.addAndUpdateListBundle import ListBundleHandler

class FolderNotFoundError(Exception):
    pass

class Metrics:
    
    def __init__(self, logFileName, logger):
        self.logFileName = logFileName
        self.start()
        self.writer = open(self.logFileName, 'a')
        self.writer.write("StepName,Time,Current Memory,Peak Memory,Used Ram Percentage\n")
        self.finalPeak = 0
        self.finalTotalTime = 0
        self.finalUsedRamPerc = 0
        self.logger = logger
    
    def start(self):
        self.startTime = time.time()
        tracemalloc.start()
    
    def getMetric(self, msg):
        
        self.endTime = time.time()
        
        self.totalTime = self.endTime - self.startTime
        
        
        current, peak = tracemalloc.get_traced_memory()
        current = current / 10**6
        peak = peak / 10**6
        
        usedRamPerc = psutil.virtual_memory()[2]
        
        self.finalPeak = max(self.finalPeak, peak)
        self.finalUsedRamPerc = max(self.finalUsedRamPerc, usedRamPerc)

        self.finalTotalTime = self.finalTotalTime + self.totalTime
        #self.finalTotalTime = round(self.finalTotalTime/60,3)
        
        outputString = f"{msg},{round(self.totalTime/60,4)} Min,{current} MB,{peak} MB,{usedRamPerc}%\n"
        
        self.logger.logFlowCheckpoint(f"{outputString}")
        
        print(f"Metrics : {outputString}")
        self.writer.write(outputString)
        tracemalloc.stop()
        tracemalloc.start()
        self.startTime = time.time()
    def end(self):
        
        current, peak = tracemalloc.get_traced_memory()
        current = current / 10**6
        outputString = f"Final Metrics,{round(self.finalTotalTime/60,4)} Min,{current} MB,{self.finalPeak} MB,{self.finalUsedRamPerc}%\n"
        print(f"Metrics : {outputString}")
        self.logger.logFlowCheckpoint(f"{outputString}")
        self.writer.write(outputString)
        self.writer.close()
        tracemalloc.stop()
        
        


def convertToInt(x):
    try:
        return str(int(x))
    except:
        return x


def convertCollectionToDataFrame(collection):

    dfExtractedHier = pd.DataFrame(collection)
    dfExtractedHier['parent_id'] = dfExtractedHier['parent_id'].apply(
        lambda x: convertToInt(x))
    dfExtractedHier['id'] = dfExtractedHier['id'].apply(
        lambda x: convertToInt(x))

    return dfExtractedHier

def getRandomString(N):
    str_ = ''.join(random.choice(string.ascii_uppercase + string.digits
                                 + string.ascii_lowercase) for _ in range(N))
    return str_


def convertHtmlToJson(controlBasePath,
                      basePath,
                      domain,
                      procedureType,
                      languageCode,
                      htmlDocName,
                      fileNameQrd,
                      fileNameLog,
                      NAPDocumentNumber):

    module_path = os.path.join(basePath)

    if "/" in basePath:
        pathSep = "/"
    else:
        pathSep = "\\"
    
    # Generate output folder path
    output_json_path = os.path.join(basePath, 'outputJSON')

    """
        Check if input folder exists, else throw exception
    """
    if(os.path.exists(module_path)):
        filenames = glob.glob(os.path.join(module_path, htmlDocName))

        # Create language specific folder in outputJSON folder if it doesn't exist
        if(not os.path.exists(output_json_path)):
            os.mkdir(output_json_path)
        logger = MatchLogger(f'Parser_{getRandomString(1)}', htmlDocName,
                             domain, procedureType, languageCode, "HTML", fileNameLog)
        
        ###################################
        #########  STEP 2 START  ##########
        
        styleLogger = MatchLogger(
            f'Style Dictionary_{getRandomString(1)}', htmlDocName, domain, procedureType, languageCode, "HTML", fileNameLog)
        if procedureType == "CAP":
            styleRulesObj = StyleRulesDictionary(logger=styleLogger,
                                                 controlBasePath=controlBasePath,
                                                 language=languageCode,
                                                 fileName=fileNameQrd,
                                                 domain=domain,
                                                 procedureType=procedureType)
        else:
            if NAPDocumentNumber == None:
                raise Exception("Missing NAPDocumentNumber")
            
            styleRulesObj = StyleRulesDictionary(logger=styleLogger,
                                                 controlBasePath=controlBasePath,
                                                 language=languageCode,
                                                 fileName=fileNameQrd,
                                                 domain=domain,
                                                 procedureType=procedureType,
                                                 NAPDocumentNumber = NAPDocumentNumber
                                                 )
        
        ###############  END   ############
        
        ###################################        
        #########  STEP 3 START ###########
        
        parserObj = parserExtractor(config, logger, styleRulesObj.styleRuleDict,
                                    styleRulesObj.styleFeatureKeyList,
                                    styleRulesObj.qrd_section_headings)
        
        for input_filename in filenames:
          # if(input_filename.find('Kalydeco II-86-PI-clean')!=-1):
            output_filename = os.path.join(output_json_path, htmlDocName)
            style_filepath =  output_filename.replace('.html','.txt')
            style_filepath =  style_filepath.replace('.txtl','.txt')
            style_filepath =  style_filepath.replace('.htm','.txt')
            print("-------------",style_filepath,"-----------------")

            output_filename = output_filename.replace('.html', '.json')
            output_filename = output_filename.replace('.htm', '.json')
            print(input_filename, output_filename)
            parserObj.createPIJsonFromHTML(input_filepath=input_filename,
                                           output_filepath=output_filename,
                                           style_filepath = style_filepath,
                                           img_base64_dict=parserObj.convertImgToBase64(input_filename)
                                           )
        #return parserObj, input_filename, output_filename, style_filepath
        return output_filename.split(pathSep)[-1], style_filepath
    
        ##############  END ###############
    else:
        try:    
            raise FolderNotFoundError(module_path + " not found")
        except:  
            logger.logFlowCheckpoint("Folder For Language Code Not Found In Input File")
            logger.logException("Folder For Language Code Not Found In Input File")
        raise FolderNotFoundError(module_path + " not found")
        return None


def splitJson(controlBasePath, basePath, domain, procedureType, languageCode, fileNameJson, fileNameQrd, fileNameLog):

    styleLogger = MatchLogger(
        f'Style Dictionary_{getRandomString(1)}', fileNameJson, domain, procedureType, languageCode, "Json", fileNameLog)

    styleRulesObj = StyleRulesDictionary(logger=styleLogger,
                                        controlBasePath=controlBasePath,
                                        language=languageCode,
                                        fileName=fileNameQrd,
                                        domain=domain,
                                        procedureType=procedureType
                                        )
    
    path_json = os.path.join(basePath,'outputJSON', fileNameJson)
    print("PathJson",path_json)
    partitionLogger = MatchLogger(
        f'Partition_{getRandomString(1)}', fileNameJson, domain, procedureType, languageCode, "Json", fileNameLog)

    partitioner = DocTypePartitioner(partitionLogger, domain, procedureType)

    partitionedJsonPaths = partitioner.partitionHtmls(
        styleRulesObj.qrd_section_headings, path_json)

    return partitionedJsonPaths


def extractAndValidateHeadings(controlBasePath,
                                basePath,
                                domain,
                                procedureType,
                                languageCode,
                                documentNumber,
                                fileNameDoc,
                                fileNameQrd,
                                fileNameMatchRuleBook,
                                fileNameDocumentTypeNames,
                                fileNameLog,
                                stopWordFilterLen=6,
                                isPackageLeaflet=False,
                                medName=None
                                ):

    if documentNumber == 0:
        topHeadingsConsidered = 4
        bottomHeadingsConsidered = 6
    elif documentNumber == 1:
        topHeadingsConsidered = 3
        bottomHeadingsConsidered = 5
    elif documentNumber == 2:
        topHeadingsConsidered = 5
        bottomHeadingsConsidered = 15
    else:
        topHeadingsConsidered = 5
        bottomHeadingsConsidered = 10

    print(f"Starting Heading Extraction For File :- {fileNameDoc}")
    logger = MatchLogger(f"Heading Extraction {fileNameDoc}_{getRandomString(1)}", fileNameDoc, domain, procedureType, languageCode, documentNumber, fileNameLog)
    logger.logFlowCheckpoint("Starting Heading Extraction")
    
    ###################################
    #########  STEP 4 #################
    
    
    stopWordlanguage = DocumentTypeNames(
        controlBasePath=controlBasePath,
        fileNameDocumentTypeNames=fileNameDocumentTypeNames,
        languageCode=languageCode,
        domain=domain,
        procedureType=procedureType,
        documentNumber=documentNumber
        ).extractStopWordLanguage()
    
    ###########  END   ################

    ###################################
    #########  STEP 5 #################
    
    
    matchDocObj = MatchDocument(
        logger,
        controlBasePath,
        basePath,
        domain,
        procedureType,
        languageCode,
        documentNumber,
        fileNameDoc,
        fileNameQrd,
        fileNameMatchRuleBook,
        fileNameDocumentTypeNames,
        topHeadingsConsidered,
        bottomHeadingsConsidered,
        stopWordFilterLen,
        stopWordlanguage,
        isPackageLeaflet,
        medName)
    df, coll, documentType, documentTypeForUI = matchDocObj.matchHtmlHeaddingsWithQrd()
    
    ###########  END   ################

    return df, coll, documentType, documentTypeForUI

def parseDocument(controlBasePath,
                  basePath,
                  htmlDocName,
                  fileNameQrd,
                  fileNameMatchRuleBook,
                  fileNameDocumentTypeNames,
                  jsonTempFileName,
                  listBundleDocumentTypeCodesFileName,
                  apiMmgtBaseUrl,
                  getListApiEndPointUrlSuffix,
                  addUpdateListApiEndPointUrlSuffix,
                  addBundleApiEndPointUrlSuffix,
                  sporApiMgmtApiBaseUrl,
                  pmsApiEndpointSuffix, 
                  smsApiEndpointSuffix,
                  localCredsJson,
                  medName = None,
                  NAPDocumentNumber=None):
    
    listRegulatedAuthCodesAccrossePI = []
    
    if "/" in basePath:
        pathSep = "/"        
    else:
        pathSep = "\\"
    
    fileNameLog = os.path.join(basePath,'FinalLog.txt')

    pathComponents = basePath.split(pathSep)
    print(pathComponents, htmlDocName)
    timestamp = pathComponents[-1]
    languageCode =  pathComponents[-2]
    medName = pathComponents[-3]
    procedureType = pathComponents[-4]
    domain = pathComponents[-5]

    print(timestamp, languageCode, medName, procedureType, domain)
        
    flowLogger =  MatchLogger(f"Flow Logger HTML_{getRandomString(1)}", htmlDocName, domain, procedureType, languageCode, "HTML", fileNameLog)
    
    metrics = Metrics(os.path.join(basePath,'Metrics.csv'),flowLogger)
    
    
    flowLogger.logFlowCheckpoint("Starting HTML Conversion To Json")
    ###Convert Html to Json
    
    ###################################
    #### Perform Steps 2&3 ############
    
    
    fileNameJson, stylesFilePath = convertHtmlToJson(controlBasePath, basePath, domain, procedureType, languageCode, htmlDocName, fileNameQrd, fileNameLog, NAPDocumentNumber)
    
    #############  END ################
    print("stylePath:-",stylesFilePath)
    flowLogger.logFlowCheckpoint("Completed HTML Conversion To Json")
    metrics.getMetric("HTML Conversion To Json")
    
    
    
    if procedureType == "CAP":
        
        ###################################
        ### OPTIONAL STEP Split Json ######
        
        
        flowLogger.logFlowCheckpoint("Starting Json Split")

        ###Split Uber Json to multiple Jsons for each category.
        partitionedJsonPaths = splitJson(controlBasePath, basePath, domain, procedureType, languageCode, fileNameJson, fileNameQrd, fileNameLog)

        partitionedJsonPaths = [ path.split(pathSep)[-1] for path in partitionedJsonPaths]
        flowLogger.logFlowCheckpoint(str(partitionedJsonPaths))

        flowLogger.logFlowCheckpoint("Completed Json Split")
        metrics.getMetric("Split Json")
        #############  END ################
        flowLogger.logFlowCheckpoint("Started Processing CAP Partitioned Jsons")
        
    else:       

        # Create the partitioned json for NAP which will be the same as output json as there is only one document.

        with open(os.path.join(basePath,'outputJSON',fileNameJson)) as f:
            json_html = json.load(f)
        dfPartitioned = pd.DataFrame(json_html['data'])

        if(not os.path.exists(os.path.join(basePath, 'partitionedJSONs'))):
            os.mkdir(os.path.join(basePath, 'partitionedJSONs'))

        dfPartitioned.to_json(os.path.join(basePath, 'partitionedJSONs', fileNameJson), orient ='records')
        partitionedJsonPaths = [fileNameJson]
        flowLogger.logFlowCheckpoint("Started Processing NAP Json")
        
    
    previous_pms_oms_annotation_data  = None
    for index, fileNamePartitioned in enumerate(partitionedJsonPaths):
        print("Index", index)
        #if index in [0,1]:
        #    continue
        if procedureType != "CAP":
            index = int(NAPDocumentNumber)
        flowLogger.logFlowCheckpoint(f"\n\n\n\n||||||||||||||||||||||||||||||||{str(index)} ||||| {str(fileNamePartitioned)}||||||||||||||||||||||||||||||||\n\n\n\n")
        
        if index == 3:
            stopWordFilterLen = 100
            isPackageLeaflet = True
        else:
            stopWordFilterLen = 6
            isPackageLeaflet = False
        
        ###################################
        #### Perform Steps 4&5 ############
        
        df, coll, documentType, documentTypeForUI = extractAndValidateHeadings(controlBasePath,
                                    basePath,
                                    domain,
                                    procedureType,
                                    languageCode,
                                    index,
                                    fileNamePartitioned,
                                    fileNameQrd,
                                    fileNameMatchRuleBook,
                                    fileNameDocumentTypeNames,
                                    fileNameLog,
                                    stopWordFilterLen=stopWordFilterLen,
                                    isPackageLeaflet=isPackageLeaflet,
                                    medName=medName)
        #return df, coll, documentType, documentTypeForUI
        print(f"Completed Heading Extraction For File")
        flowLogger.logFlowCheckpoint("Completed Heading Extraction For File")
        metrics.getMetric(f"{index}: Heading Extraction")
        ############# END #################

        
        ###################################
        #########  STEP 6 START ###########
    
        print(f"Starting Document Annotation For File :- {fileNamePartitioned}")        
        flowLogger.logFlowCheckpoint("Starting Document Annotation For File")
        documentAnnotationObj = DocumentAnnotation(fileNamePartitioned,
                                                   localCredsJson['PmsSubscriptionKey'],
                                                   localCredsJson['SmsSubscriptionKey'],
                                                   sporApiMgmtApiBaseUrl,
                                                   pmsApiEndpointSuffix,
                                                   smsApiEndpointSuffix,
                                                   df,
                                                   coll,
                                                   domain,
                                                   procedureType,
                                                   index)
        
        pms_oms_annotation_data = documentAnnotationObj.processRegulatedAuthorizationForDoc()
        print(pms_oms_annotation_data)
        
        if pms_oms_annotation_data == None:
            pms_oms_annotation_data = previous_pms_oms_annotation_data
        else:
            previous_pms_oms_annotation_data = pms_oms_annotation_data
        
       
        
        print(f"Completed Document Annotation")        
        flowLogger.logFlowCheckpoint("Completed Document Annotation")
        metrics.getMetric(f"{index}: Document Annotation")
        #############  END ################
        
        ###################################
        #########  STEP 7 START ###########
        print(f"Starting Extracting Content Between Heading For File :- {fileNamePartitioned}")        
        flowLogger.logFlowCheckpoint("Starting Extracting Content Between Heading")
        
        extractContentlogger =  MatchLogger(f'ExtractContentBetween_{index}_{getRandomString(1)}', fileNamePartitioned, domain, procedureType, languageCode, index, fileNameLog)
        extractorObj = DataBetweenHeadingsExtractor(extractContentlogger, basePath, coll)
        dfExtractedHierRR = extractorObj.extractContentBetweenHeadings(fileNamePartitioned)
        
        print(f"Completed Extracting Content Between Heading")        
        flowLogger.logFlowCheckpoint("Completed Extracting Content Between Heading")
        metrics.getMetric(f"{index}: Content Extraction")
        
        ########### END ###################
        
        
        ###################################
        #########  STEP 8 START ###########
        
        listBundleDocumentTypeCodesFilePath = os.path.join(controlBasePath,
                                                                listBundleDocumentTypeCodesFileName.split(".")[0],
                                                                listBundleDocumentTypeCodesFileName)
        with open(listBundleDocumentTypeCodesFilePath, encoding='utf-8') as f:
            listBundleDocumentTypeCodes = json.load(f)
            
        bundleDocumentTypeCode = listBundleDocumentTypeCodes[domain][str(index)]['listBundleCode']
        bundleMetaData = {'pmsOmsAnnotationData':pms_oms_annotation_data,
                          'documentTypeCode': bundleDocumentTypeCode,
                          'documentType': documentTypeForUI,
                          'languageCode': languageCode,
                          'medName': medName}
        
        
        ############# END #################
        
        
        ###################################
        #########  STEP 9 START ###########
        
        xmlLogger =  MatchLogger(f'XmlGeneration_{index}_{getRandomString(1)}', fileNamePartitioned, domain, procedureType, languageCode, index, fileNameLog)
        
        fhirXmlGeneratorObj = FhirXmlGenerator(xmlLogger, controlBasePath, basePath, bundleMetaData, stylesFilePath)
        fileNameXml = fileNamePartitioned.replace('.json','.xml')
        generatedXml = fhirXmlGeneratorObj.generateXml(dfExtractedHierRR, fileNameXml)
        
        metrics.getMetric(f"{index}: Generate XML")
        
        ########### END ###################
        
        ###################################
        #########  STEP 10 START ##########
        
        fhirServiceLogger =  MatchLogger(f'XML Submission Logger_{index}_{getRandomString(1)}', fileNamePartitioned, domain, procedureType, languageCode, index, fileNameLog)
        
        fhirServiceObj = FhirService(fhirServiceLogger, apiMmgtBaseUrl, addBundleApiEndPointUrlSuffix, localCredsJson['apiMmgtSubsKey'], basePath, generatedXml)
        fhirServiceObj.submitFhirXml()
        
        metrics.getMetric(f"{index}: Submit FHIR Msg")
        
        print(f"Created XML File For :- {fileNamePartitioned}")
        
        ############## END ################
        
        ###################################
        #########  STEP 11 START ##########
        flowLogger.logFlowCheckpoint("Starting list bundle update/addition")
        if documentAnnotationObj.listRegulatedAuthorizationIdentifiers != None:
            for id in documentAnnotationObj.listRegulatedAuthorizationIdentifiers:
                listRegulatedAuthCodesAccrossePI.append(id)
        listBundleLogger =  MatchLogger(f'List Bundle Creation Logger_{index}_{getRandomString(1)}', fileNamePartitioned, domain, procedureType, languageCode, index, fileNameLog)
        print("\nlistRegulatedAuthCodesAccrossePI",listRegulatedAuthCodesAccrossePI)
        try:
            listBundleHandler = ListBundleHandler(listBundleLogger,
                     domain,
                     procedureType,
                     index,
                     documentType,
                     documentTypeForUI,
                     languageCode,
                     medName,
                     controlBasePath,
                     jsonTempFileName,
                     listBundleDocumentTypeCodesFileName,
                     fileNameDocumentTypeNames,
                     listRegulatedAuthCodesAccrossePI,
                     apiMmgtBaseUrl,
                     getListApiEndPointUrlSuffix,
                     addUpdateListApiEndPointUrlSuffix,
                     localCredsJson['apiMmgtSubsKey'])

            listBundleXml = listBundleHandler.addOrUpdateDocumentItem(str(fhirServiceObj.SubmittedFhirMsgRefId), pms_oms_annotation_data)
            print(listBundleXml)
            listBundleHandler.submitListXmLToServer(listBundleXml)

            flowLogger.logFlowCheckpoint("Completed list bundle update/addition")
            metrics.getMetric(f"{index}: Update/Add List Bundle")
                    #return df,coll,dfExtractedHierRR
                
        ################ END #############
        
        except Exception as e:
            print(str(e))
            if 'No MAN Code found' in str(e):
                flowLogger.logFlowCheckpoint("Skipping list bundle addtion/update as no MAN found")
            
    
    flowLogger.logFlowCheckpoint("Completed Processing Partitioned Jsons")
    metrics.getMetric(f"{index}: Completed")
    metrics.end()

In [4]:
#####################################
######### Perform All Steps #########
def runAll(inputList):
    for inputDoc in inputList:
        # inputZipFolderPath = "F:\Projects\EMA\Repository\EMA EPI PoC\\function_code\\inputblob"
        inputZipFolderPath = os.path.abspath(os.path.join('..'))
        inputZipFolderPath = os.path.join(inputZipFolderPath, 'inputblob')
        inputZipFileName = inputDoc

        fileNameQrd = 'qrd_canonical_model.csv'
        fileNameMatchRuleBook = 'ruleDict.json'
        fileNameLocalCreds = "localCredentialsDev.json"
        fileNameDocumentTypeNames = 'documentTypeNames.json'
        fsMountName = '/mounted'
        jsonTempFileName = 'listBundleJsonTemplate.json'
        listBundleDocumentTypeCodesFileName = 'listBundleDocumentTypeCodes.json'
        apiMmgtBaseUrl = "https://ema-dap-epi-dev-fhir-apim.azure-api.net"
        getListApiEndPointUrlSuffix = "/epi/v1/List"
        addUpdateListApiEndPointUrlSuffix = "/epi-w/v1/List"
        addBundleApiEndPointUrlSuffix = "/epi-w/v1/Bundle"
        
        sporApiMgmtApiBaseUrl = "https://spor-sit.azure-api.net"
        pmsApiEndpointSuffix = "/pms/api/v2/"
        smsApiEndpointSuffix = "/sms/api/v2/"
                
        info = inputZipFileName.split("~")
        ###################################
        ########  STEP 1 START ############
        ###################################
        try:
            medName = info[0]
            domain = info[1]
            procedureType = info[2]
            languageCode = info[3]
            if procedureType == "NAP":     
                NAPDocumentNumber = info[4]
                timestamp = info[5]
            else:
                timestamp = info[4]
                NAPDocumentNumber = None
                
            timestamp = timestamp.replace(".zip","")

        except Exception:
            raise f"Missing required info in the zip file name {inputZipFileName}"

        if "\\" in os.getcwd():
            localEnv = True
            inputZipFolderPath = os.path.join(os.path.abspath(os.path.join('..')),inputZipFolderPath)
            if os.path.exists(os.path.join(os.path.abspath(os.path.join('..')), 'work')):
                outputFolderPath = os.path.join(os.path.abspath(os.path.join('..')), 'work', f"{domain}", f"{procedureType}", f"{medName}", f"{languageCode}", f"{timestamp}")
            elif os.path.exists(os.path.join(os.path.abspath(os.path.join('../..')), 'work')):
                outputFolderPath = os.path.join(os.path.abspath(os.path.join('../..')), 'work', f"{domain}", f"{procedureType}", f"{medName}", f"{languageCode}", f"{timestamp}")

            if os.path.exists(os.path.join(os.path.abspath(os.path.join("..")),'control')):
                controlFolderPath = os.path.join(os.path.abspath(os.path.join('..')),'control')
            elif os.path.exists(os.path.join(os.path.abspath(os.path.join("../..")),'control')):
                controlFolderPath = os.path.join(os.path.abspath(os.path.join('../..')),'control')
            
            
        else:
            localEnv = False
            inputZipFolderPath = os.path.join(f'{fsMountName}',inputZipFolderPath)
            outputFolderPath = os.path.join(f'{fsMountName}', 'work', f"{domain}", f"{procedureType}", f"{medName}", f"{languageCode}", f"{timestamp}")
            controlFolderPath = os.path.join(f'{fsMountName}','control')

        localCredFilePath = os.path.join(controlFolderPath, 'localCredentials', fileNameLocalCreds)
        
        with open(localCredFilePath) as r:
            localCredsJson = json.load(r)
        
        metaDatakeys = set([ key for key in localCredsJson])
        requiredCredsParameters = set(['PmsSubscriptionKey','SmsSubscriptionKey','apiMmgtSubsKey','appInsightsInstrumentationKey'])
        
        if len(requiredCredsParameters - metaDatakeys) !=0:
            raise Exception(f"Missing required keys in local creds file :- {str(requiredCredsParameters-metaDatakeys)}")
        
        for key in localCredsJson:
            if len(localCredsJson[key]) == 0 or localCredsJson[key] == None:
                raise Exception(f"Missing required info in the zip file for key {key}")
        
        os.environ['APPLICATIONINSIGHTS_CONNECTION_STRING'] = localCredsJson['appInsightsInstrumentationKey']
        
        print(inputZipFileName, inputZipFolderPath, outputFolderPath, controlFolderPath)

        mode = 0o666

        if localEnv is True:
            inputZipFolderPath = inputZipFolderPath.replace("/","\\")
            outputFolderPath = outputFolderPath.replace("/","\\")
            controlFolderPath = controlFolderPath.replace("/","\\")

        try:
            os.makedirs(inputZipFolderPath, mode)
            os.makedirs(outputFolderPath, mode)
            os.makedirs(controlFolderPath, mode)

        except Exception:
            print("Already Present")

        with zipfile.ZipFile(f'{inputZipFolderPath}/{inputZipFileName}',"r") as zip_ref:
                zip_ref.extractall(outputFolderPath)


        _,_,fileNames = next(os.walk(outputFolderPath))
        htmlFileName = [fileName for fileName in fileNames if ".htm" in fileName][0]

        print(htmlFileName)

        ############### END ###############
        
        ####################################
        ####### Perform Steps #2-11 ########
        parseDocument(controlFolderPath,
                  outputFolderPath,
                  htmlFileName,
                  fileNameQrd,
                  fileNameMatchRuleBook,
                  fileNameDocumentTypeNames,
                  jsonTempFileName,
                  listBundleDocumentTypeCodesFileName,
                  apiMmgtBaseUrl,
                  getListApiEndPointUrlSuffix,
                  addUpdateListApiEndPointUrlSuffix,
                  addBundleApiEndPointUrlSuffix,
                  sporApiMgmtApiBaseUrl,
                  pmsApiEndpointSuffix, 
                  smsApiEndpointSuffix,
                  localCredsJson,
                  medName,
                  NAPDocumentNumber)
        ############ END ##################

        
##########  END ####################

In [5]:
def runAllTest(inputList):
    for inputDoc in inputList:
        # inputZipFolderPath = "F:\Projects\EMA\Repository\EMA EPI PoC\\function_code\\inputblob"
        inputZipFolderPath = os.path.abspath(os.path.join('..'))
        inputZipFolderPath = os.path.join(inputZipFolderPath, 'inputblob')
        inputZipFileName = inputDoc

        fileNameQrd = 'qrd_canonical_model.csv'
        fileNameMatchRuleBook = 'ruleDict.json'
        fileNameLocalCreds = "localCredentialsTest.json"
        fileNameDocumentTypeNames = 'documentTypeNames.json'
        fsMountName = '/mounted'
        jsonTempFileName = 'listBundleJsonTemplate.json'
        listBundleDocumentTypeCodesFileName = 'listBundleDocumentTypeCodes.json'
        apiMmgtBaseUrl = "https://ema-dap-epi-tst-fhir-apim.azure-api.net"
        getListApiEndPointUrlSuffix = "/epi/v1/List"
        addUpdateListApiEndPointUrlSuffix = "/epi-w/v1/List"
        addBundleApiEndPointUrlSuffix = "/epi-w/v1/Bundle"
        
        sporApiMgmtApiBaseUrl = "https://spor-sit.azure-api.net"
        pmsApiEndpointSuffix = "/pms/api/v2/"
        smsApiEndpointSuffix = "/sms/api/v2/"
                

        info = inputZipFileName.split("~")

        try:
            medName = info[0]
            domain = info[1]
            procedureType = info[2]
            languageCode = info[3]
            if procedureType == "NAP":     
                NAPDocumentNumber = info[4]
                timestamp = info[5]
            else:
                timestamp = info[4]
                NAPDocumentNumber = None
                
            timestamp = timestamp.replace(".zip","")

        except Exception:
            raise f"Missing required info in the zip file name {inputZipFileName}"

        if "\\" in os.getcwd():
            localEnv = True
            inputZipFolderPath = os.path.join(os.path.abspath(os.path.join('..')),inputZipFolderPath)
            outputFolderPath = os.path.join(os.path.abspath(os.path.join('..')), 'work', f"{domain}", f"{procedureType}", f"{medName}", f"{languageCode}", f"{timestamp}")
            controlFolderPath = os.path.join(os.path.abspath(os.path.join('..')),'control')
        else:
            localEnv = False
            inputZipFolderPath = os.path.join(f'{fsMountName}',inputZipFolderPath)
            outputFolderPath = os.path.join(f'{fsMountName}', 'work', f"{domain}", f"{procedureType}", f"{medName}", f"{languageCode}", f"{timestamp}")
            controlFolderPath = os.path.join(f'{fsMountName}','control')

        localCredFilePath = os.path.join(controlFolderPath, 'localCredentials', fileNameLocalCreds)
        
        with open(localCredFilePath) as r:
            localCredsJson = json.load(r)
        
        metaDatakeys = set([ key for key in localCredsJson])
        requiredCredsParameters = set(['PmsSubscriptionKey','SmsSubscriptionKey','apiMmgtSubsKey','appInsightsInstrumentationKey'])
        
        if len(requiredCredsParameters - metaDatakeys) !=0:
            raise Exception(f"Missing required keys in local creds file :- {str(requiredCredsParameters-metaDatakeys)}")
        
        for key in localCredsJson:
            if len(localCredsJson[key]) == 0 or localCredsJson[key] == None:
                raise Exception(f"Missing required info in the zip file for key {key}")
        
        os.environ['APPLICATIONINSIGHTS_CONNECTION_STRING'] = localCredsJson['appInsightsInstrumentationKey']
        
        print(inputZipFileName, inputZipFolderPath, outputFolderPath, controlFolderPath)

        mode = 0o666

        if localEnv is True:
            inputZipFolderPath = inputZipFolderPath.replace("/","\\")
            outputFolderPath = outputFolderPath.replace("/","\\")
            controlFolderPath = controlFolderPath.replace("/","\\")

        try:
            os.makedirs(inputZipFolderPath, mode)
            os.makedirs(outputFolderPath, mode)
            os.makedirs(controlFolderPath, mode)

        except Exception:
            print("Already Present")

        with zipfile.ZipFile(f'{inputZipFolderPath}/{inputZipFileName}',"r") as zip_ref:
                zip_ref.extractall(outputFolderPath)


        _,_,fileNames = next(os.walk(outputFolderPath))
        htmlFileName = [fileName for fileName in fileNames if ".htm" in fileName][0]

        print(htmlFileName)

        parseDocument(controlFolderPath,
                  outputFolderPath,
                  htmlFileName,
                  fileNameQrd,
                  fileNameMatchRuleBook,
                  fileNameDocumentTypeNames,
                  jsonTempFileName,
                  listBundleDocumentTypeCodesFileName,
                  apiMmgtBaseUrl,
                  getListApiEndPointUrlSuffix,
                  addUpdateListApiEndPointUrlSuffix,
                  addBundleApiEndPointUrlSuffix,
                  sporApiMgmtApiBaseUrl,
                  pmsApiEndpointSuffix, 
                  smsApiEndpointSuffix,
                  localCredsJson,
                  medName,
                  NAPDocumentNumber)


In [ ]:
inputList = ['ELOCTA~H~CAP~bg~2021-06-09T08-18-48Z.zip',
 'ELOCTA~H~CAP~cs~2021-06-09T09-32-50Z.zip',
 'ELOCTA~H~CAP~da~2021-06-09T09-34-52Z.zip',
 'ELOCTA~H~CAP~de~2021-06-09T09-36-33Z.zip',
 'ELOCTA~H~CAP~el~2021-06-07T06-03-45Z.zip']

runAll(inputList)

In [ ]:

runAll(['Abacavir Accord~H~NAP~sv~0~2021-05-27T10-49-42Z.zip'])


In [ ]:
runAllTest(['Cystagon~H~CAP~no~2021-06-25T14-03-22Z.zip'])

In [92]:
runAllTest(['Cystagon~H~CAP~no~2021-06-25T14-03-22Z.zip'])

2021-07-02 05:49:26,348 : Flow Logger HTML_8 : Starting HTML Conversion To Json | H | CAP |  no | HTML | Cystagon_clean.htm
2021-07-02 05:49:26,355 : Style Dictionary_j : Reading style dictionary in file: rule_dictionary_no.json | H | CAP |  no | HTML | Cystagon_clean.htm
2021-07-02 05:49:26,355 : Style Dictionary_j : Reading style dictionary in file: rule_dictionary_no.json | H | CAP |  no | HTML | Cystagon_clean.htm
2021-07-02 05:49:26,407 : Style Dictionary_j : Qrd Section Keys Retrieved For Style Dictionary: PREPARATOMTALE, VEDLEGG II, A. MERKING, B. PAKNINGSVEDLEGG | H | CAP |  no | HTML | Cystagon_clean.htm
2021-07-02 05:49:26,407 : Style Dictionary_j : Qrd Section Keys Retrieved For Style Dictionary: PREPARATOMTALE, VEDLEGG II, A. MERKING, B. PAKNINGSVEDLEGG | H | CAP |  no | HTML | Cystagon_clean.htm


Cystagon~H~CAP~no~2021-06-25T14-03-22Z.zip F:\Projects\EMA\Repository\EMA EPI PoC\function_code\inputblob F:\Projects\EMA\Repository\EMA EPI PoC\function_code\work\H\CAP\Cystagon\no\2021-06-25T14-03-22Z F:\Projects\EMA\Repository\EMA EPI PoC\function_code\control
Already Present
Cystagon_clean.htm
['F:', 'Projects', 'EMA', 'Repository', 'EMA EPI PoC', 'function_code', 'work', 'H', 'CAP', 'Cystagon', 'no', '2021-06-25T14-03-22Z'] Cystagon_clean.htm
2021-06-25T14-03-22Z no Cystagon CAP H
ind 6539
qrd_df    index     id domain Procedure type    Document type Language code  \
0   2562  76001      H            CAP             SmPC            no   
1   2622  77001      H            CAP         Annex II            no   
2   2635  78001      H            CAP        Labelling            no   
3   2668  79001      H            CAP  Package leaflet            no   

  Display_code             Name  parent_id  Mandatory  heading_id  
0          NaN   PREPARATOMTALE        NaN       True           

2021-07-02 05:49:26,998 : Parser_c : Style Information Stored In File: F:\Projects\EMA\Repository\EMA EPI PoC\function_code\work\H\CAP\Cystagon\no\2021-06-25T14-03-22Z\outputJSON\Cystagon_clean.txt | H | CAP |  no | HTML | Cystagon_clean.htm


Dom Text                                                                                                                                                                                                                                                                                                                                                                                                                                                                                         
Dom Text 
Dom Text 
Dom Text 
Dom Text 
Dom Text 
Dom Text 
Dom Text 
Dom Text 
Dom Text 
Dom Text 
Dom Text 
Dom Text 
Dom Text 
Dom Text 
Dom Text 
Dom Text 
Dom Text 
Dom Text 
Dom Text 
Dom Text 
Dom Text 
Dom Text 
Dom Text VEDLEGG I
Dom Text 
Dom Text PREPARATOMTALE
Dom Text 
Dom Text  
Dom Text 
Dom Text 1.    LEGEMIDLETS NAVN
Dom Text 
totalLen 28
text_with_req []
Cystagon 50 mg harde kapsler | 28 False
match None
False
styleCharCount 7 28
uppercase perctange in given element is 25.0
[]
Dom Text Cystagon 

totalLen 387
text_with_req []
Tilfeller av Ehlers-Danlos-lignende syndrom og vaskulære forstyrrelser på albuene er blitt rapportert hos barn behandlet med høye doser av forskjellige formuleringer av cysteamin (cysteamin klorhydrat eller cysteamin eller cysteamin bitartrat) som regel over den maksimale dosen 1,95 g/m | 287 False
match None
False
styleCharCount 47 287
2 | 1 False
match None
False
styleCharCount 1 1
!!!!!!!!!!!!!!!!!!!!!!!!
/dag. Disse hudlesjonene var assosiert med vaskulær proliferasjon, hudstria og lesjoner i benvevet. | 99 False
match None
False
styleCharCount 13 99
uppercase perctange in given element is 15.8
[1]
Dom Text Tilfeller av Ehlers-Danlos-lignende syndrom og vaskulære forstyrrelser på albuene er blitt rapportert hos barn behandlet med høye doser av forskjellige formuleringer av cysteamin (cysteamin klorhydrat eller cysteamin eller cysteamin bitartrat) som regel over den maksimale dosen 1,95 g/m 2 /dag. Disse hudlesjonene var assosiert med vaskulær prolifera

...

POST sucessful: XML added with id 88659e08-2c2a-49e9-a6da-84dec58c5093
Metrics : 1: Submit FHIR Msg,0.0224 Min,0.261968 MB,0.375695 MB,49.6%

Created XML File For :- Cystagon_clean_VEDLEGG II.json

listRegulatedAuthCodesAccrossePI ['EU/1/97/039/001', 'EU/1/97/039/002', 'EU/1/97/039/003', 'EU/1/97/039/004']


2021-07-02 05:51:16,137 : List Bundle Creation Logger_1_b : Getting list bundle for MAN EU/1/97/039/002  | H | CAP |  no | 1 | Cystagon_clean_VEDLEGG II.json
2021-07-02 05:51:17,157 : List Bundle Creation Logger_1_b : Getting list bundle for MAN EU/1/97/039/003  | H | CAP |  no | 1 | Cystagon_clean_VEDLEGG II.json
2021-07-02 05:51:18,159 : List Bundle Creation Logger_1_b : Getting list bundle for MAN EU/1/97/039/004  | H | CAP |  no | 1 | Cystagon_clean_VEDLEGG II.json
2021-07-02 05:51:19,163 : List Bundle Creation Logger_1_b : Getting Existing List Bundle using common list id 5793a889-b407-4a69-9c0b-ac35d1d199eb | H | CAP |  no | 1 | Cystagon_clean_VEDLEGG II.json
2021-07-02 05:51:20,336 : List Bundle Creation Logger_1_b : Added missing MAN identifiers | H | CAP |  no | 1 | Cystagon_clean_VEDLEGG II.json
2021-07-02 05:51:20,338 : List Bundle Creation Logger_1_b : Upated domain | H | CAP |  no | 1 | Cystagon_clean_VEDLEGG II.json
2021-07-02 05:51:20,339 : List Bundle Creation Logger_1_

Skipping updating active substance as none was found in the pms data
b'<List xmlns="http://hl7.org/fhir"><id value="5793a889-b407-4a69-9c0b-ac35d1d199eb" /><identifier><system value="http://spor.ema.europa.eu/v2/medicine-name" /><value value="cystagon" /></identifier><identifier><system value="http://spor.ema.europa.eu/v2/marketing-authorisation-numbers" /><value value="EU/1/97/039/001" /></identifier><identifier><system value="http://spor.ema.europa.eu/v2/marketing-authorisation-numbers" /><value value="EU/1/97/039/002" /></identifier><identifier><system value="http://spor.ema.europa.eu/v2/marketing-authorisation-numbers" /><value value="EU/1/97/039/003" /></identifier><identifier><system value="http://spor.ema.europa.eu/v2/marketing-authorisation-numbers" /><value value="EU/1/97/039/004" /></identifier><identifier><system value="http://spor.ema.europa.eu/v2/marketing-authorisation-numbers" /><value value="EU/1/97/039/001-" /></identifier><identifier><system value="http://spor.ema.eur

2021-07-02 05:51:21,756 : List Bundle Creation Logger_1_b : List update successfully completed 5793a889-b407-4a69-9c0b-ac35d1d199eb | H | CAP |  no | 1 | Cystagon_clean_VEDLEGG II.json
2021-07-02 05:51:21,757 : Flow Logger HTML_8 : Completed list bundle update/addition | H | CAP |  no | HTML | Cystagon_clean.htm
2021-07-02 05:51:21,759 : Flow Logger HTML_8 : 1: Update/Add List Bundle,0.1102 Min,0.483554 MB,0.754314 MB,50.0%
 | H | CAP |  no | HTML | Cystagon_clean.htm
2021-07-02 05:51:21,762 : Flow Logger HTML_8 : Completed Processing Partitioned Jsons | H | CAP |  no | HTML | Cystagon_clean.htm
2021-07-02 05:51:21,764 : Flow Logger HTML_8 : 3: Completed,0.0 Min,0.004494 MB,0.152704 MB,50.0%
 | H | CAP |  no | HTML | Cystagon_clean.htm
2021-07-02 05:51:21,769 : Flow Logger HTML_8 : Final Metrics,1.9229 Min,0.0 MB,6.922931 MB,50.0%
 | H | CAP |  no | HTML | Cystagon_clean.htm


Metrics : 1: Update/Add List Bundle,0.1102 Min,0.483554 MB,0.754314 MB,50.0%

Index 2
Index 3
Metrics : 3: Completed,0.0 Min,0.004494 MB,0.152704 MB,50.0%

Metrics : Final Metrics,1.9229 Min,0.0 MB,6.922931 MB,50.0%



In [34]:
runAllTest(['Metacam~V~CAP~en~2021-05-17T11-36-04Z.zip'])

2021-07-02 22:38:30,037 : Flow Logger HTML_j : Starting HTML Conversion To Json | V | CAP |  en | HTML | Metacam~V~CAP~en.htm
2021-07-02 22:38:30,048 : Style Dictionary_m : Reading style dictionary in file: rule_dictionary_en.json | V | CAP |  en | HTML | Metacam~V~CAP~en.htm
2021-07-02 22:38:30,048 : Style Dictionary_m : Reading style dictionary in file: rule_dictionary_en.json | V | CAP |  en | HTML | Metacam~V~CAP~en.htm
2021-07-02 22:38:30,048 : Style Dictionary_m : Reading style dictionary in file: rule_dictionary_en.json | V | CAP |  en | HTML | Metacam~V~CAP~en.htm
2021-07-02 22:38:30,108 : Style Dictionary_m : Qrd Section Keys Retrieved For Style Dictionary: SUMMARY OF PRODUCT CHARACTERISTICS, ANNEX II, A. LABELLING , B. PACKAGE LEAFLET: | V | CAP |  en | HTML | Metacam~V~CAP~en.htm
2021-07-02 22:38:30,108 : Style Dictionary_m : Qrd Section Keys Retrieved For Style Dictionary: SUMMARY OF PRODUCT CHARACTERISTICS, ANNEX II, A. LABELLING , B. PACKAGE LEAFLET: | V | CAP |  en | HTM

Metacam~V~CAP~en~2021-05-17T11-36-04Z.zip F:\Projects\EMA\Repository\EMA EPI PoC\function_code\inputblob F:\Projects\EMA\Repository\EMA EPI PoC\function_code\work\V\CAP\Metacam\en\2021-05-17T11-36-04Z F:\Projects\EMA\Repository\EMA EPI PoC\function_code\control
Already Present
Metacam~V~CAP~en.htm
['F:', 'Projects', 'EMA', 'Repository', 'EMA EPI PoC', 'function_code', 'work', 'V', 'CAP', 'Metacam', 'en', '2021-05-17T11-36-04Z'] Metacam~V~CAP~en.htm
2021-05-17T11-36-04Z en Metacam CAP V
ind 6539
qrd_df    index    id domain Procedure type    Document type Language code  \
0      0     1      V            CAP             SmPC            en   
1     41  1001      V            CAP         Annex II            en   
2     51  2001      V            CAP        Labelling            en   
3     85  3001      V            CAP  Package leaflet            en   

  Display_code                                Name  parent_id  Mandatory  \
0          NaN  SUMMARY OF PRODUCT CHARACTERISTICS        NaN

totalLen 5
text_with_req []
Pigs: | 5 False
match None
False
styleCharCount 1 5
uppercase perctange in given element is 20.0
[]
Dom Text Pigs:
section_dict defaultdict(<class 'list'>, {'SUMMARY OF PRODUCT CHARACTERISTICS': True, 'ANNEX II': False, 'A. LABELLING ': False, 'B. PACKAGE LEAFLET:': False})
Section Found SUMMARY OF PRODUCT CHARACTERISTICS
Best Place
Section Not Found ANNEX II
Section Not Found A. LABELLING 
Section Not Found B. PACKAGE LEAFLET:
~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~
totalLen 98
text_with_req []
For use in non-infectious locomotor disorders to reduce the symptoms of lameness and inflammation. | 98 False
match None
False
styleCharCount 15 98
uppercase perctange in given element is 15.299999999999999
[]
Dom Text For use in non-infectious locomotor disorders to reduce the symptoms of lameness and inflammation.
section_dict defaultdict(<class 'list'>, {'SUMMARY OF PRODUCT CHARACTERISTICS': True, 'ANNEX II': False, 'A. LABELLING ': False, 'B. PACKAGE LEA

totalLen 103
text_with_req []
Special precautions to be taken by the person administering the veterinary medicinal product to animals | 103 False
match None
False
styleCharCount 15 103
uppercase perctange in given element is 14.6
[]
Dom Text Special precautions to be taken by the person administering the veterinary medicinal product to animals
section_dict defaultdict(<class 'list'>, {'SUMMARY OF PRODUCT CHARACTERISTICS': True, 'ANNEX II': False, 'A. LABELLING ': False, 'B. PACKAGE LEAFLET:': False})
Section Found SUMMARY OF PRODUCT CHARACTERISTICS
Best Place
Section Not Found ANNEX II
Section Not Found A. LABELLING 
Section Not Found B. PACKAGE LEAFLET:
~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~
totalLen 193
text_with_req []
Accidental self-injection may give rise to pain. People with known hypersensitivity to non-steroidal anti-inflammatory drugs (NSAIDs) should avoid contact with the veterinary medicinal product. | 193 False
match None
False
styleCharCount 35 193
uppercase per

totalLen 60
text_with_req []
Pigs: | 5 False
match None
False
styleCharCount 1 5
            Can be used during pregnancy and lactation. | 55 False
match None
False
styleCharCount 19 55
uppercase perctange in given element is 33.300000000000004
[]
Dom Text             Can be used during pregnancy and lactation.
section_dict defaultdict(<class 'list'>, {'SUMMARY OF PRODUCT CHARACTERISTICS': True, 'ANNEX II': False, 'A. LABELLING ': False, 'B. PACKAGE LEAFLET:': False})
~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~
Dom Text 
section_dict defaultdict(<class 'list'>, {'SUMMARY OF PRODUCT CHARACTERISTICS': True, 'ANNEX II': False, 'A. LABELLING ': False, 'B. PACKAGE LEAFLET:': False})
Section Found SUMMARY OF PRODUCT CHARACTERISTICS
Best Place
Section Not Found ANNEX II
Section Not Found A. LABELLING 
Section Not Found B. PACKAGE LEAFLET:
~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~
totalLen 80
text_with_req []
4.8     Interaction with other medicinal products and other forms of inte

...


OriginalCheck


OriginalCheck



2021-07-02 22:42:25,209 : Flow Logger HTML_j : Completed Heading Extraction For File | V | CAP |  en | HTML | Metacam~V~CAP~en.htm
2021-07-02 22:42:25,209 : Flow Logger HTML_j : 2: Heading Extraction,2.9865 Min,2.756247 MB,6.716276 MB,50.3%
 | V | CAP |  en | HTML | Metacam~V~CAP~en.htm
2021-07-02 22:42:25,221 : Flow Logger HTML_j : Starting Document Annotation For File | V | CAP |  en | HTML | Metacam~V~CAP~en.htm



OriginalCheck


OriginalCheck



Heading Not Found 
 ['nan,MINIMUM PARTICULARS TO APPEAR ON BLISTERS OR STRIPS,29']


dict_keys([])
Completed Heading Extraction For File
Metrics : 2: Heading Extraction,2.9865 Min,2.756247 MB,6.716276 MB,50.3%

Starting Document Annotation For File :- Metacam~V~CAP~en_ LABELLING .json
dfAuthHeadingsSmPC      index    id Procedure type Display code  \
17      68  2018            CAP           16   
35      68  2018            CAP           16   
61      68  2018            CAP           16   
79      68  2018            CAP           16   
106     68  2018            CAP           16   
133     68  2018            CAP           16   
159     68  2018            CAP           16   
177     68  2018            CAP           16   
195     68  2018            CAP           16   
222     68  2018            CAP           16   
245     68  2018            CAP           16   
272     68  2018            CAP           16   
299     68  2018            CAP      

Found entry with code 220000000061
Found Packaged Product Definition
Missing Key 'holder' in entry key value pair
processedOutputIndirect [((None, None), '31772')]
Found following active ingredients ids for medicine product id 600000002358 
 ['59150']
Found entry with code 220000000061
Found Packaged Product Definition
Missing Key 'holder' in entry key value pair
processedOutputIndirect [((None, None), '31773')]
Found following active ingredients ids for medicine product id 600000002358 
 ['59150']
Found entry with code 220000000061
Found Packaged Product Definition
Missing Key 'holder' in entry key value pair
processedOutputIndirect [((None, None), '31775')]
Found following active ingredients ids for medicine product id 600000002358 
 ['59150']
Found entry with code 220000000061
Found Packaged Product Definition
Missing Key 'holder' in entry key value pair
processedOutputIndirect [((None, None), '31774')]
Found following active ingredients ids for medicine product id 600000002358 
 ['

ConnectionError: HTTPSConnectionPool(host='spor-sit.azure-api.net', port=443): Max retries exceeded with url: /sms/api/v2//SubstanceDefinition/100000092098 (Caused by NewConnectionError('<urllib3.connection.HTTPSConnection object at 0x000002819D72CD60>: Failed to establish a new connection: [WinError 10060] A connection attempt failed because the connected party did not properly respond after a period of time, or established connection failed because connected host has failed to respond'))

In [6]:
inputList = ['ELOCTA~H~CAP~bg~2021-06-09T08-18-48Z.zip',
 'ELOCTA~H~CAP~cs~2021-06-09T09-32-50Z.zip',
 'ELOCTA~H~CAP~da~2021-06-09T09-34-52Z.zip',
 'ELOCTA~H~CAP~de~2021-06-09T09-36-33Z.zip',
 'ELOCTA~H~CAP~el~2021-06-07T06-03-45Z.zip']

runAll(inputList)

2021-06-24 03:37:50,101 : Flow Logger HTML_o : Starting HTML Conversion To Json | H | CAP |  bg | HTML | Elocta_clean.htm
2021-06-24 03:37:50,109 : Style Dictionary_A : Reading style dictionary in file: rule_dictionary_bg.json | H | CAP |  bg | HTML | Elocta_clean.htm
2021-06-24 03:37:50,190 : Style Dictionary_A : Qrd Section Keys Retrieved For Style Dictionary: КРАТКА ХАРАКТЕРИСТИКА НА ПРОДУКТА, ПРИЛОЖЕНИЕ II, A. ДАННИ ВЪРХУ ОПАКОВКАТА, Б.  ЛИСТОВКА | H | CAP |  bg | HTML | Elocta_clean.htm


ELOCTA~H~CAP~bg~2021-06-09T08-18-48Z.zip D:\Projects\EMA\Repository\EMA EPI PoC\function_code\inputblob D:\Projects\EMA\Repository\EMA EPI PoC\function_code\work\H\CAP\ELOCTA\bg\2021-06-09T08-18-48Z D:\Projects\EMA\Repository\EMA EPI PoC\function_code\control
Already Present
Elocta_clean.htm
['D:', 'Projects', 'EMA', 'Repository', 'EMA EPI PoC', 'function_code', 'work', 'H', 'CAP', 'ELOCTA', 'bg', '2021-06-09T08-18-48Z'] Elocta_clean.htm
2021-06-09T08-18-48Z bg ELOCTA CAP H
------------- D:\Projects\EMA\Repository\EMA EPI PoC\function_code\work\H\CAP\ELOCTA\bg\2021-06-09T08-18-48Z\outputJSON\Elocta_clean.txt -----------------
D:\Projects\EMA\Repository\EMA EPI PoC\function_code\work\H\CAP\ELOCTA\bg\2021-06-09T08-18-48Z\Elocta_clean.htm D:\Projects\EMA\Repository\EMA EPI PoC\function_code\work\H\CAP\ELOCTA\bg\2021-06-09T08-18-48Z\outputJSON\Elocta_clean.json


2021-06-24 03:37:51,901 : Parser_L : Style Information Stored In File: D:\Projects\EMA\Repository\EMA EPI PoC\function_code\work\H\CAP\ELOCTA\bg\2021-06-09T08-18-48Z\outputJSON\Elocta_clean.txt | H | CAP |  bg | HTML | Elocta_clean.htm


!!!!!!!!!!! IN TABLE !!!!!!!!!!!!!!!!!
!!!!!!!!!!! IN TABLE !!!!!!!!!!!!!!!!!
!!!!!!!!!!! IN TABLE !!!!!!!!!!!!!!!!!
!!!!!!!!!!! IN TABLE !!!!!!!!!!!!!!!!!
!!!!!!!!!!! IN TABLE !!!!!!!!!!!!!!!!!
!!!!!!!!!!! IN TABLE !!!!!!!!!!!!!!!!!


2021-06-24 03:38:02,135 : Parser_L : Writing to file: D:\Projects\EMA\Repository\EMA EPI PoC\function_code\work\H\CAP\ELOCTA\bg\2021-06-09T08-18-48Z\outputJSON\Elocta_clean.json | H | CAP |  bg | HTML | Elocta_clean.htm
2021-06-24 03:38:02,750 : Flow Logger HTML_o : Completed HTML Conversion To Json | H | CAP |  bg | HTML | Elocta_clean.htm
2021-06-24 03:38:02,752 : Flow Logger HTML_o : HTML Conversion To Json,0.2109 Min,7.776406 MB,19.400294 MB,79.4%
 | H | CAP |  bg | HTML | Elocta_clean.htm
2021-06-24 03:38:02,769 : Flow Logger HTML_o : Starting Json Split | H | CAP |  bg | HTML | Elocta_clean.htm
2021-06-24 03:38:02,775 : Style Dictionary_v : Reading style dictionary in file: rule_dictionary_bg.json | H | CAP |  bg | Json | Elocta_clean.json
2021-06-24 03:38:02,827 : Style Dictionary_v : Qrd Section Keys Retrieved For Style Dictionary: КРАТКА ХАРАКТЕРИСТИКА НА ПРОДУКТА, ПРИЛОЖЕНИЕ II, A. ДАННИ ВЪРХУ ОПАКОВКАТА, Б.  ЛИСТОВКА | H | CAP |  bg | Json | Elocta_clean.json
2021-06-24 03:3

...

Metrics : 3: Update/Add List Bundle,0.2608 Min,0.211574 MB,0.53975 MB,71.2%

Metrics : 3: Completed,0.0 Min,0.14956 MB,0.152213 MB,71.2%

Metrics : Final Metrics,5.3906 Min,0.0 MB,20.170449 MB,73.2%

ELOCTA~H~CAP~el~2021-06-07T06-03-45Z.zip D:\Projects\EMA\Repository\EMA EPI PoC\function_code\inputblob D:\Projects\EMA\Repository\EMA EPI PoC\function_code\work\H\CAP\ELOCTA\el\2021-06-07T06-03-45Z D:\Projects\EMA\Repository\EMA EPI PoC\function_code\control
Already Present
Elocta_clean.htm
['D:', 'Projects', 'EMA', 'Repository', 'EMA EPI PoC', 'function_code', 'work', 'H', 'CAP', 'ELOCTA', 'el', '2021-06-07T06-03-45Z'] Elocta_clean.htm
2021-06-07T06-03-45Z el ELOCTA CAP H


2021-06-24 04:01:08,792 : Style Dictionary_v : Qrd Section Keys Retrieved For Style Dictionary: ΠΕΡΙΛΗΨΗ ΤΩΝ ΧΑΡΑΚΤΗΡΙΣΤΙΚΩΝ ΤΟΥ ΠΡΟΪΟΝΤΟΣ, ΠΑΡΑΡΤΗΜΑ ΙΙ, Α. ΕΠΙΣΗΜΑΝΣΗ, Β. ΦΥΛΛΟ ΟΔΗΓΙΩΝ ΧΡΗΣΗΣ | H | CAP |  el | HTML | Elocta_clean.htm
2021-06-24 04:01:08,792 : Style Dictionary_v : Qrd Section Keys Retrieved For Style Dictionary: ΠΕΡΙΛΗΨΗ ΤΩΝ ΧΑΡΑΚΤΗΡΙΣΤΙΚΩΝ ΤΟΥ ΠΡΟΪΟΝΤΟΣ, ΠΑΡΑΡΤΗΜΑ ΙΙ, Α. ΕΠΙΣΗΜΑΝΣΗ, Β. ΦΥΛΛΟ ΟΔΗΓΙΩΝ ΧΡΗΣΗΣ | H | CAP |  el | HTML | Elocta_clean.htm


------------- D:\Projects\EMA\Repository\EMA EPI PoC\function_code\work\H\CAP\ELOCTA\el\2021-06-07T06-03-45Z\outputJSON\Elocta_clean.txt -----------------
D:\Projects\EMA\Repository\EMA EPI PoC\function_code\work\H\CAP\ELOCTA\el\2021-06-07T06-03-45Z\Elocta_clean.htm D:\Projects\EMA\Repository\EMA EPI PoC\function_code\work\H\CAP\ELOCTA\el\2021-06-07T06-03-45Z\outputJSON\Elocta_clean.json


2021-06-24 04:01:11,123 : Parser_I : Style Information Stored In File: D:\Projects\EMA\Repository\EMA EPI PoC\function_code\work\H\CAP\ELOCTA\el\2021-06-07T06-03-45Z\outputJSON\Elocta_clean.txt | H | CAP |  el | HTML | Elocta_clean.htm


KeyError: 'ΠΑΡΑΡΤΗΜΑ ΙΙ'